<a href="https://colab.research.google.com/github/HinataKikuchi/Governor-of-Tokyo-Cup/blob/main/main.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# [都知事杯 -- Open Data Hackathon](https://portal.data.metro.tokyo.lg.jp/hackathon/)

## Member

- [hyudai28](https://github.com/hyudai28)

- [Hinata Kikuchi](https://github.com/HinataKikuchi)

- [fujishit](https://github.com/fujishit)

## Theme

[東京都のオープンデータカタログ](https://portal.data.metro.tokyo.lg.jp/)を用いて、東京都内の消火栓数等を表示しました。


In [3]:
# グーグルドライブのマウント(接続)
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [4]:
# 地図用モジュールのインストール
%pip install folium

## 必要なモジュールのimport

In [5]:
# import系
import pandas as pd # DataFrameとして値を受け取る
import requests # URLから値を受け取るときに必要になるモジュール
import io # データから値を取り出すためのモジュール
import folium # 地図を出力するためのモジュール
from folium.plugins import MarkerCluster # 地図を出力するためのモジュール

## URLの設定

In [6]:
# URL系 ここにcsvファイルのURLを書く
# 東京都内の各市町村の木造建築数を保存したcsv
wooden_house_statistics_URL = 'http://www.toshiseibi.metro.tokyo.jp/bosai/data/mokuzou2.csv'
# 消火栓位置を保存したcsv
fire_prevention_things_URL = 'https://www.opendata.metro.tokyo.lg.jp/shoubou/2021/130001_fire-hydrant.csv'
# 日本の各自治体の面積を保存したcsv
Japan_area_csv_URL = 'http://www.gsi.go.jp/KOKUJYOHO/MENCHO/backnumber/R1_R3_all_mencho.csv'

## URL先のcsvの読み込み

In [7]:
# URL先のcsvの読み込み
# 東京都の木造建築の数
r = requests.get(wooden_house_statistics_URL)
# データフレームとして保存
wooden_house_df = pd.read_csv(io.BytesIO(r.content),encoding='shift-jis',sep=",")

In [8]:
# 消火栓と防火水槽の場所(緯度経度)
r = requests.get(fire_prevention_things_URL)
# データフレームとして保存
fire_prevention_df = pd.read_csv(io.BytesIO(r.content),encoding='utf-8',sep=",")

In [9]:
# 全国の市区町村の面積(km^2)
r = requests.get(Japan_area_csv_URL)
# データフレームとして保存
Japaan_area_df = pd.read_csv(io.BytesIO(r.content),encoding='cp932',sep=",", header=4)

## データの確認

In [10]:
# 東京都内の木造建築の面積
wooden_house_df.head(3)

区  番号        地区名  面積(ha)          事業期間
0  新宿区   1     若葉・須賀町    15.6   平成5年度〜令和6年度
1  台東区   2  谷中二・三・五丁目    28.7  平成14年度〜令和7年度
2  墨田区   3       北部中央   184.5  昭和59年度〜令和7年度

In [11]:
# 東京都内の消火栓の位置
fire_prevention_df.head(3)

種別         緯度          経度
0  消火栓  35.690628  139.761033
1  消火栓  35.689614  139.761005
2  消火栓  35.690625  139.759017

In [12]:
# 東京都の各市区町村の面積
Japaan_area_df[Japaan_area_df['都道府県']=='東京都'].head(3)

標準地域コード 都道府県 郡･支庁･振興局等  ... 令和元年10月1日備考  令和元年7月面積(k㎡) 令和元年7月備考
807   13000  東京都       NaN  ...       （参考値）       2194.07    （参考値）
811   13101  東京都       NaN  ...       （参考値）         11.66    （参考値）
812   13102  東京都       NaN  ...       （参考値）         10.21    （参考値）

[3 rows x 20 columns]

## 試しに消火栓位置を特定

In [18]:
def visualize_locations(df, # データフレーム
                        longitude_column_name, # データフレームの中で緯度を保存したカラム名
                        latitude_column_name, # データフレームの中で経度を保存したカラム名
                        zoom=4, # ズームの大きさ、デフォルトで4
                        idx_range = 15000 # 出力する行数の上限
                        ) -> folium.folium.Map: # Foliumのマップ型を返す
    """
    EXPLAIN : 日本を拡大した地図に、pandasデータフレームのlatitudeおよびlongitudeカラムをプロットする。
    ARGS :
    % df, # データフレーム
    % longitude_column_name, # データフレームの中で緯度を保存したカラム名
    % latitude_column_name, # データフレームの中で経度を保存したカラム名
    % zoom=4, # ズームの大きさ、デフォルトで4
    idx_range = 15000 # 出力する行数の上限
    """
        	
    # 図の大きさを指定する。
    f = folium.Figure(width=1000, height=500)

    # 初期表示の中心の座標を指定して地図を作成する。
    center_lat=35.690628
    center_lon=139.761033
    # foliumのMap形のコンストラクタに初期の座標とズーム情報を渡す, fは図の大きさとして指定
    m = folium.Map([center_lat,center_lon], zoom_start=zoom).add_to(f)
    marker_cluster = MarkerCluster().add_to(m)
    # データフレームの全ての行のマーカーを作成する。
    # 総データ数の10分の1だけのデータを扱う、つまり1万3千程度、これ以上だと出力できない事態が発生する。
    if df.shape[0] < idx_range : # 出力上限よりデータフレームの行数が小さい場合はデータフレームの行数分だけ出力する
      for idx in range(df.shape[0]):
        folium.Marker(location=[df[longitude_column_name][idx], df[latitude_column_name][idx]]).add_to(marker_cluster)
    else:
      for idx in range(idx_range): # データフレームの行数が出力上限以上の場合は出力上限分だけ出力する
        folium.Marker(location=[df[longitude_column_name][idx], df[latitude_column_name][idx]]).add_to(marker_cluster)

    return m

In [13]:
# 消火栓位置の情報、13万行あるのでちょっと多すぎる、出力数を抑えることにした
fire_prevention_df.shape

(135344, 3)

In [36]:
# 緯度経度のデータを渡し、小さなデータとして出力する、データ総数の10分の1のデータを出力する
visualize_locations(fire_prevention_df, '緯度', '経度',zoom=11, idx_range=fire_prevention_df.shape[0]//10)

In [37]:
# 東京都内すべての消火栓データをhtmlとして保存する、保存されたhtmlをブラウザで開けば東京都内の消火栓位置を見ることができる
visualize_locations(fire_prevention_df, '緯度', '経度',zoom=11, idx_range=fire_prevention_df.shape[0]).save('map.html')